<a href="https://colab.research.google.com/github/viicctor91/me.github.io/blob/main/TFM_DsMarket.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install plotly_express

#  DS MARKET

In [ ]:
from IPython.display import Image
Image(url='https://drive.google.com/file/d/1vKxw6n6g7qONVFM31BULB93n7zXzliA1/view?usp=sharing', width=700, height=400)

# Montando Drive

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Importando Pacotes

In [3]:
# Bibliotecas de manipulação de dados
import gc
import os
import pandas as pd
import numpy as np

# Bibliotecas de visualização de dados
import cufflinks as cf
import matplotlib.pyplot as plt
import plotly
import plotly_express as px
import plotly.graph_objects as go
import plotly.io as pio
import plotly.offline as py
import seaborn as sns
from plotly.subplots import make_subplots
#from plotly.offline import init_notebook_mode

# Bibliotecas de modelagem e pré-processamento
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
# from kneed import KneeLocator
# from pandas_profiling import ProfileReport

# Outras bibliotecas e configurações
import logging
import math
import multiprocessing as mp
import shutil
from tqdm import tqdm

# Configurações do notebook e bibliotecas
%matplotlib inline
#cf.go_offline()
#init_notebook_mode(connected=True)
pd.set_option('display.max_columns', None)
# pio.renderers.default = 'colab'


#Lendo todos os dados usando pandas

## **df_sales**

In [ ]:
df_sales = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/item_sales.csv")

## **df_prices**

In [ ]:
df_prices = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/item_prices.csv")

## **df_calendar**

In [ ]:
df_calendar = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/daily_calendar_with_events.csv")

Aqui usamos o erro ponderado médio quadrático em escala (WRMSSE).
Usamos WRMSSE em vez de RMSE simples (Root Mean Squared Error) porque neste conjunto de dados há muitas vendas zero, então mesmo que nosso modelo preveja a maioria das vendas próximas de zero, nosso modelo terá um bom desempenho, o WRMSSE leva isso em consideração.
Além disso, o WRMSSE é escalado de forma independente e, portanto, não é afetado pela escala de cada série.
É também uma métrica simétrica, pois penaliza todas as previsões positivas, negativas, grandes e positivas.

# Downcasting

# Redução de Tipo (Downcasting)
Nesta seção, vou fazer a redução de tipo dos dataframes para diminuir a quantidade de armazenamento utilizado por eles e também para acelerar as operações realizadas sobre eles.

- **Colunas Numéricas:** Dependendo do seu ambiente, o pandas cria automaticamente colunas int32, int64, float32 ou float64 para as numéricas. Se você conhece o valor mínimo ou máximo de uma coluna, você pode usar um subtipo que consome menos memória. Você também pode usar um subtipo sem sinal (unsigned) se não houver valor negativo.<br>
Aqui estão os diferentes subtipos que você pode usar:<br>
`int8 / uint8`: consome 1 byte de memória, varia entre -128/127 ou 0/255<br>
`bool`: consome 1 byte, verdadeiro ou falso<br>
`float16 / int16 / uint16`: consome 2 bytes de memória, varia entre -32768 e 32767 ou 0/65535<br>
`float32 / int32 / uint32`: consome 4 bytes de memória, varia entre -2147483648 e 2147483647<br>
`float64 / int64 / uint64`: consome 8 bytes de memória<br>
Se uma de suas colunas tem valores entre 1 e 10, por exemplo, você reduzirá o tamanho dessa coluna de 8 bytes por linha para 1 byte, o que é uma economia de memória de mais de 85% nessa coluna!
- **Colunas Categóricas:** O pandas armazena colunas categóricas como objetos. Uma das razões pelas quais esse armazenamento não é otimizado é que ele cria uma lista de ponteiros para o endereço de memória de cada valor da sua coluna. Para colunas com baixa cardinalidade (a quantidade de valores únicos é menor que 50% da contagem desses valores), isso pode ser otimizado forçando o pandas a usar uma tabela de mapeamento virtual, onde todos os valores únicos são mapeados através de um número inteiro, em vez de um ponteiro. Isso é feito usando o tipo de dado "category".


In [ ]:
sales_bd = np.round(df_sales.memory_usage().sum()/(1024*1024),1)
calendar_bd = np.round(df_calendar.memory_usage().sum()/(1024*1024),1)
prices_bd = np.round(df_prices.memory_usage().sum()/(1024*1024),1)

NameError: ignored

In [ ]:
#Downcast in order to save memory
def downcast(df):
    cols = df.dtypes.index.tolist()
    types = df.dtypes.values.tolist()
    for i,t in enumerate(types):
        if 'int' in str(t):
            if df[cols[i]].min() > np.iinfo(np.int8).min and df[cols[i]].max() < np.iinfo(np.int8).max:
                df[cols[i]] = df[cols[i]].astype(np.int8)
            elif df[cols[i]].min() > np.iinfo(np.int16).min and df[cols[i]].max() < np.iinfo(np.int16).max:
                df[cols[i]] = df[cols[i]].astype(np.int16)
            elif df[cols[i]].min() > np.iinfo(np.int32).min and df[cols[i]].max() < np.iinfo(np.int32).max:
                df[cols[i]] = df[cols[i]].astype(np.int32)
            else:
                df[cols[i]] = df[cols[i]].astype(np.int64)
        elif 'float' in str(t):
            if df[cols[i]].min() > np.finfo(np.float16).min and df[cols[i]].max() < np.finfo(np.float16).max:
                df[cols[i]] = df[cols[i]].astype(np.float16)
            elif df[cols[i]].min() > np.finfo(np.float32).min and df[cols[i]].max() < np.finfo(np.float32).max:
                df[cols[i]] = df[cols[i]].astype(np.float32)
            else:
                df[cols[i]] = df[cols[i]].astype(np.float64)
        elif t == object:
            if cols[i] == 'date':
                df[cols[i]] = pd.to_datetime(df[cols[i]], format='%Y-%m-%d')
            else:
                df[cols[i]] = df[cols[i]].astype('category')
    return df

df_sales = downcast(df_sales)
df_prices = downcast(df_prices)
df_calendar = downcast(df_calendar)

In [ ]:
sales_ad = np.round(df_sales.memory_usage().sum()/(1024*1024),1)
calendar_ad = np.round(df_calendar.memory_usage().sum()/(1024*1024),1)
prices_ad = np.round(df_prices.memory_usage().sum()/(1024*1024),1)

NameError: ignored

O gráfico abaixo mostra o quanto o downcasting afetou o uso de memória dos DataFrames. Claramente, conseguimos reduzir sales e prices para menos de 1/4 de seu uso de memória real. calendar já é um DataFrame pequeno.

In [ ]:
dic = {'DataFrame':['df_sales','df_calendar','df_prices'],
       'Antes do downcasting':[sales_bd,calendar_bd,prices_bd],
       'Depois do downcasting':[sales_ad,calendar_ad,prices_ad]}

memory = pd.DataFrame(dic)
memory = pd.melt(memory, id_vars='DataFrame', var_name='Status', value_name='Memory (MB)')
memory.sort_values('Memory (MB)',inplace=True)
fig = px.bar(memory, x='DataFrame', y='Memory (MB)', color='Status', barmode='group', text='Memory (MB)')
fig.update_traces(texttemplate='%{text} MB', textposition='outside')
fig.update_layout(template='seaborn', title=' Efeito do Downcasting')
fig.show()

NameError: ignored

## Dicionário de dados

File 1 – item_sales.csv

| Name | Description |
| --- | --- |
| id | sales series id (combination of item + store_code) |
| item | product id |
| category | product category |
| department | department id (different identifier for different stores) |
| store | store name |
| store_code | store id |
| region | region |
| d_1,d_2,d_... | number of units sold per day |

File 2 – item_prices.csv

| Name | Description |
| --- | --- |
| item | product id |
| category | product category |
| store_code | alphanumeric code of the store |
| yearweek | date period for the price (year-week format) |
| sell_price |	price for the product “item” for the period in “yearweek”. * |

* Prices are provided per week (average across 7 days). If not available, there were no sales for the product during that week ludes an event, the name of this event (only a few are included).

File 3 – daily_calendar_with_events.csv

| Name | Description |
| --- | --- |
| date | date in y-m-d format |
| weekday |	day of the week |
| weekday_int |	numeric day of the week (Saturday day 1, Friday day 7) |
| d	| day identifier |
| event | if the date includes an event, the name of this event (only a few are included) |

# Pré-processamento e exploração de dados

# Item Prices

In [ ]:
# Primeiras cinco linhas do df
df_prices.head()

item    category store_code  yearweek  sell_price
0  ACCESORIES_1_001  ACCESORIES      NYC_1  201328.0     12.7414
1  ACCESORIES_1_001  ACCESORIES      NYC_1  201329.0     12.7414
2  ACCESORIES_1_001  ACCESORIES      NYC_1  201330.0     10.9858
3  ACCESORIES_1_001  ACCESORIES      NYC_1  201331.0     10.9858
4  ACCESORIES_1_001  ACCESORIES      NYC_1  201332.0     10.9858

In [ ]:
# Cinco ultimas linhas
df_prices.tail()

item     category store_code  yearweek  sell_price
6965701  SUPERMARKET_3_827  SUPERMARKET      PHI_3       NaN         1.2
6965702  SUPERMARKET_3_827  SUPERMARKET      PHI_3       NaN         1.2
6965703  SUPERMARKET_3_827  SUPERMARKET      PHI_3       NaN         1.2
6965704  SUPERMARKET_3_827  SUPERMARKET      PHI_3       NaN         1.2
6965705  SUPERMARKET_3_827  SUPERMARKET      PHI_3       NaN         1.2

In [ ]:
# Dimensão do df
df_prices.shape

(6965706, 5)

In [ ]:
df_prices.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6965706 entries, 0 to 6965705
Data columns (total 5 columns):
 #   Column      Dtype  
---  ------      -----  
 0   item        object 
 1   category    object 
 2   store_code  object 
 3   yearweek    float64
 4   sell_price  float64
dtypes: float64(2), object(3)
memory usage: 265.7+ MB


### Função para observar cada coluna do df_prices

In [ ]:
def observar(data, column, count=True):
    print(f"======== Observações para a coluna '{column}' ========")

    # Tipo de dados da coluna
    column_type = data[column].dtype
    print(f"\n- Tipo de Dados: {column_type}")

    # Contagem de valores únicos
    unique_values = data[column].unique()
    print(f"\n- Quantidade de Valores Únicos: {len(unique_values)}")

    # Visualização dos valores únicos (limitado para não sobrecarregar a saída)
    if len(unique_values) > 10:
        print(f"  (Mostrando 10 dos {len(unique_values)} valores únicos)")
        print(f"- Valores Únicos: {unique_values[:10]} ...")
    else:
        print(f"- Valores Únicos: {unique_values}")

    # Contagem de valores nulos
    null_count = data[column].isnull().sum()
    print(f"\n- Quantidade de Valores Nulos: {null_count}")

    # Estatísticas básicas, se a coluna for numérica
    if np.issubdtype(column_type, np.number):
        print(f"\n- Estatísticas Básicas:")
        print(data[column].describe())

    # Contagem de ocorrências de cada valor
    if count:
        value_counts = data[column].value_counts()
        print(f"\n- Contagem de Valores:")
        print(value_counts)

    print("=====================================================")


#### Item

In [ ]:
observar(df_prices, 'item')

======== Observações para a coluna 'item' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 3049
  (Mostrando 10 dos 3049 valores únicos)
- Valores Únicos: ['ACCESORIES_1_001' 'ACCESORIES_1_002' 'ACCESORIES_1_003'
 'ACCESORIES_1_004' 'ACCESORIES_1_005' 'ACCESORIES_1_006'
 'ACCESORIES_1_007' 'ACCESORIES_1_008' 'ACCESORIES_1_009'
 'ACCESORIES_1_010'] ...

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
SUPERMARKET_3_587      2870
HOME_&_GARDEN_1_177    2870
HOME_&_GARDEN_2_283    2870
ACCESORIES_1_337       2870
SUPERMARKET_1_032      2870
                       ... 
HOME_&_GARDEN_1_308     652
HOME_&_GARDEN_1_159     633
HOME_&_GARDEN_1_242     610
SUPERMARKET_3_296       602
SUPERMARKET_2_379       543
Name: item, Length: 3049, dtype: int64


____

#### Category

In [ ]:
observar(df_prices, 'category')

======== Observações para a coluna 'category' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 3
- Valores Únicos: ['ACCESORIES' 'HOME_&_GARDEN' 'SUPERMARKET']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
SUPERMARKET      3239821
HOME_&_GARDEN    2418627
ACCESORIES       1307258
Name: category, dtype: int64


#### store_code  

In [ ]:
observar(df_prices, 'store_code')

======== Observações para a coluna 'store_code' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 10
- Valores Únicos: ['NYC_1' 'NYC_2' 'NYC_3' 'NYC_4' 'BOS_1' 'BOS_2' 'BOS_3' 'PHI_1' 'PHI_2'
 'PHI_3']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
BOS_2    713960
BOS_1    712527
NYC_1    711073
PHI_3    708747
NYC_3    706585
BOS_3    703682
NYC_4    691375
PHI_2    690546
PHI_1    678209
NYC_2    649002
Name: store_code, dtype: int64


#### yearweek    

In [ ]:
 pd.set_option('display.max_rows', None)
 pd.reset_option('display.max_rows')

In [ ]:
observar(df_calendar, 'yearweek')

======== Observações para a coluna 'date' ========

- Tipo de Dados: datetime64[ns]

- Quantidade de Valores Únicos: 1913
- Valores Únicos: ['2011-01-29T00:00:00.000000000' '2011-01-30T00:00:00.000000000'
 '2011-01-31T00:00:00.000000000' ... '2016-04-22T00:00:00.000000000'
 '2016-04-23T00:00:00.000000000' '2016-04-24T00:00:00.000000000']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
2011-01-29    1
2014-07-23    1
2014-08-04    1
2014-08-03    1
2014-08-02    1
             ..
2012-10-24    1
2012-10-23    1
2012-10-22    1
2012-10-21    1
2016-04-24    1
Name: date, Length: 1913, dtype: int64


#### sell_price

In [ ]:
observar(df_prices, 'sell_price')

======== Observações para a coluna 'sell_price' ========

- Tipo de Dados: float64

- Quantidade de Valores Únicos: 1892
  (Mostrando 10 dos 1892 valores únicos)
- Valores Únicos: [12.7414 10.9858 11.1454  5.2801  3.9501  5.7722  6.1712  3.9634  3.2984
  4.0964] ...

- Quantidade de Valores Nulos: 0

- Estatísticas Básicas:
count    6.965706e+06
mean     5.518273e+00
std      4.387861e+00
min      1.200000e-02
25%      2.620100e+00
50%      4.200000e+00
75%      7.176000e+00
max      1.341500e+02
Name: sell_price, dtype: float64

- Contagem de Valores:
2.3760     221088
3.5760     217873
3.0000     189541
1.2000     150387
4.7760     142487
            ...  
5.1875          1
4.7500          1
14.8625         1
16.5750         1
2.2800          1
Name: sell_price, Length: 1892, dtype: int64


##### Tratamento da coluna yearweek

Temos ums grande quantidade de dados faltando na coluna yearweek

In [ ]:
#verificando valores em falta
soma_missings_por_coluna = df_prices.isnull().sum()
soma_missings_por_coluna

item          0
category      0
store_code    0
yearweek      0
sell_price    0
dtype: int64

In [ ]:
# Calculando a porcentagem de dados faltantes para a coluna 'yearweek'
tamanho_df_prices = len(df_prices)
percentagem_faltante = round(soma_missings_por_coluna['yearweek'] / tamanho_df_prices * 100, 2)

# Exibindo o resultado
print(f"A porcentagem de dados faltantes para a coluna 'yearweek' é {percentagem_faltante}%.")
print(f"Isso corresponde a {soma_missings_por_coluna['yearweek']} de {tamanho_df_prices} registros.")


A porcentagem de dados faltantes para a coluna 'yearweek' é 3.5%.
Isso corresponde a 243920 de 6965706 registros.


A coluna yearweek possui datas faltando no ano de 2016, que vai da semana 18 a semana 25. no total de 8 datas por item, como são 3090 items e os items se repetem pelas 10 lojas, por isso temos um total de 243920 datas em falta.

In [ ]:
# Definir a sequência de yearweeks que serão usados para preencher os dados faltantes
sequence = ['201618.0', '201619.0', '201620.0', '201621.0', '201622.0', '201623.0', '201624.0', '201625.0']

# Preencher os NaN na coluna 'yearweek' com a sequência
df_prices['yearweek'].fillna(pd.Series(sequence * (len(df_prices) // len(sequence) + 1))[:len(df_prices)], inplace=True)


In [ ]:
# Convertendo a coluna 'yearweek' para o tipo string
df_prices['yearweek'] = df_prices['yearweek'].astype(str)

# Mantenha apenas os 6 primeiros caracteres na coluna 'yearweek', removendo o .0 no final de cada data
df_prices['yearweek'] = df_prices['yearweek'].str.slice(0, 6)

In [ ]:
# Ordenando o dataframe pela coluna yearweek
df_prices.sort_values('yearweek', inplace=True)

# Exiba o DataFrame reordenado
display(df_prices)

item       category store_code yearweek  sell_price
471545     SUPERMARKET_2_189    SUPERMARKET      NYC_1   201105    3.000000
5890184  HOME_&_GARDEN_2_316  HOME_&_GARDEN      PHI_2   201105    9.585938
2136969     ACCESORIES_1_323     ACCESORIES      NYC_4   201105    6.476562
3956461    SUPERMARKET_2_240    SUPERMARKET      BOS_2   201105    2.255859
1624599  HOME_&_GARDEN_2_074  HOME_&_GARDEN      NYC_3   201105    1.212891
...                      ...            ...        ...      ...         ...
1993751    SUPERMARKET_3_503    SUPERMARKET      NYC_3   201625    2.976562
805167      ACCESORIES_1_408     ACCESORIES      NYC_2   201625    0.797852
4101927    SUPERMARKET_3_463    SUPERMARKET      BOS_2   201625    7.199219
4101711    SUPERMARKET_3_462    SUPERMARKET      BOS_2   201625    1.200195
4641119    SUPERMARKET_2_134    SUPERMARKET      BOS_3   201625    3.576172

[6965706 rows x 5 columns]

## Exportanto csvs apos Downcasting e tratamento da coluna yearweek

In [ ]:
# Salva o DataFrame como um arquivo CSV no Google Drive
df_prices.to_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_prices.csv", index=False)

In [ ]:
df_sales.to_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_sales.csv", index=False)

In [ ]:
df_calendar.to_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_calendar.csv", index=False)

# Importando df's modificados

In [ ]:
df_sales = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_sales.csv")
df_prices = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_prices.csv")
df_calendar = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_calendar.csv")

# Item sales

In [ ]:
# Primeiras cinco linhas do df
df_sales.head()

id              item    category    department  \
0  ACCESORIES_1_001_NYC_1  ACCESORIES_1_001  ACCESORIES  ACCESORIES_1   
1  ACCESORIES_1_002_NYC_1  ACCESORIES_1_002  ACCESORIES  ACCESORIES_1   
2  ACCESORIES_1_003_NYC_1  ACCESORIES_1_003  ACCESORIES  ACCESORIES_1   
3  ACCESORIES_1_004_NYC_1  ACCESORIES_1_004  ACCESORIES  ACCESORIES_1   
4  ACCESORIES_1_005_NYC_1  ACCESORIES_1_005  ACCESORIES  ACCESORIES_1   

               store store_code    region  d_1  d_2  d_3  d_4  d_5  d_6  d_7  \
0  Greenwich_Village      NYC_1  New York    0    0    0    0    0    0    0   
1  Greenwich_Village      NYC_1  New York    0    0    0    0    0    0    0   
2  Greenwich_Village      NYC_1  New York    0    0    0    0    0    0    0   
3  Greenwich_Village      NYC_1  New York    0    0    0    0    0    0    0   
4  Greenwich_Village      NYC_1  New York    0    0    0    0    0    0    0   

   d_8  d_9  d_10  d_11  d_12  d_13  d_14  d_15  d_16  d_17  d_18  d_19  d_20  \
0    0    0     0     0     0     0     0     0     0     0     0     0     0   
1    0    0     0     0     0     0     0     0     0     0     0     0     0   
2    0    0     0     0     0     0     0     0     0     0     0     0     0   
3    0    0     0     0     0     0     0     0     0     0     0     0     0   
4    0    0     0     0     0     0     0     0     0     0     0     0     0   

   d_21  d_22  d_23  d_24  d_25  d_26  d_27  d_28  d_29  d_30  d_31  d_32  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0     0   
3     0     0     0     0     0     0     0     0     0     0     0     0   
4     0     0     0     0     0     0     0     0     0     0     0     0   

   d_33  d_34  d_35  d_36  d_37  d_38  d_39  d_40  d_41  d_42  d_43  d_44  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0     0   
3     0     0     0     0     2     0     0     0     2     0     1     0   
4     0     0     0     0     0     0     0     0     0     0     0     0   

   d_45  d_46  d_47  d_48  d_49  d_50  d_51  d_52  d_53  d_54  d_55  d_56  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0     0   
3     0     0     0     0     0     2     0     1     0     0     1     1   
4     0     0     0     0     0     0     0     0     0     0     0     0   

   d_57  d_58  d_59  d_60  d_61  d_62  d_63  d_64  d_65  d_66  d_67  d_68  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0     0   
3     1     0     2     3     1     0     0     0     0     0     1     0   
4     0     0     0     0     0     0     0     0     0     0     0     0   

   d_69  d_70  d_71  d_72  d_73  d_74  d_75  d_76  d_77  d_78  d_79  d_80  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0     0   
3     0     1     1     0     0     1     0     0     1     2     3     0   
4     0     0     0     0     0     0     0     0     0     0     0     0   

   d_81  d_82  d_83  d_84  d_85  d_86  d_87  d_88  d_89  d_90  d_91  d_92  \
0     0     0     0     0     0     0     0     0     0     0     0     0   
1     0     0     0     0     0     0     0     0     0     0     0     0   
2     0     0     0     0     0     0     0     0     0     0     0   

In [ ]:
# Cinco ultimas linhas
df_sales.tail()

id               item     category     department  \
30485  SUPERMARKET_3_823_PHI_3  SUPERMARKET_3_823  SUPERMARKET  SUPERMARKET_3   
30486  SUPERMARKET_3_824_PHI_3  SUPERMARKET_3_824  SUPERMARKET  SUPERMARKET_3   
30487  SUPERMARKET_3_825_PHI_3  SUPERMARKET_3_825  SUPERMARKET  SUPERMARKET_3   
30488  SUPERMARKET_3_826_PHI_3  SUPERMARKET_3_826  SUPERMARKET  SUPERMARKET_3   
30489  SUPERMARKET_3_827_PHI_3  SUPERMARKET_3_827  SUPERMARKET  SUPERMARKET_3   

               store store_code        region  d_1  d_2  d_3  d_4  d_5  d_6  \
30485  Queen_Village      PHI_3  Philadelphia    0    0    2    2    0    3   
30486  Queen_Village      PHI_3  Philadelphia    0    0    0    0    0    5   
30487  Queen_Village      PHI_3  Philadelphia    0    6    0    2    2    4   
30488  Queen_Village      PHI_3  Philadelphia    0    0    0    0    0    0   
30489  Queen_Village      PHI_3  Philadelphia    0    0    0    0    0    0   

       d_7  d_8  d_9  d_10  d_11  d_12  d_13  d_14  d_15  d_16  d_17  d_18  \
30485    1    4    1     0     0     3     4     4     0     0     1     0   
30486    0    1    1     3     1     1     0     4     2     0     1     2   
30487    1    8    5     2     7     5     3     5    20     8    10     3   
30488    0    0    0     0     0     0     0     0     0     0     0     0   
30489    0    0    0     0     0     0     0     0     0     0     0     0   

       d_19  d_20  d_21  d_22  d_23  d_24  d_25  d_26  d_27  d_28  d_29  d_30  \
30485     1     1     7     7     3     6     3     3     7    12     4     2   
30486     1     1     0     0     0     0     3     1     1     1     2     0   
30487     3     4     7     2     3     5     6     3     4     1     2     5   
30488     0     0     0     0     0     0     0     0     0     0     0     0   
30489     0     0     0     0     0     0     0     0     0     0     0     0   

       d_31  d_32  d_33  d_34  d_35  d_36  d_37  d_38  d_39  d_40  d_41  d_42  \
30485     7     5    12     5     3     3     7     6     4     6     3     6   
30486     1     0     1     1     1     3     3     4     4     3     6     1   
30487     1     2     2     2     1     9     8     1     6     3     3     4   
30488     0     0     0     0     0     0     0     0     0     0     0     0   
30489     0     0     0     0     0     0     0     0     0     0     0     0   

       d_43  d_44  d_45  d_46  d_47  d_48  d_49  d_50  d_51  d_52  d_53  d_54  \
30485     2     3     4     1     1     3     2     1     2     3     4     7   
30486     0     1     2     3     0     1     1     1     0     0     0     1   
30487    10     4     6     3     2     1     1     3     2     2     1     1   
30488     0     0     0     0     0     0     0     0     0     0     0     0   
30489     0     0     0     0     0     0     0     0     0     0     0     0   

       d_55  d_56  d_57  d_58  d_59  d_60  d_61  d_62  d_63  d_64  d_65  d_66  \
30485     2     4     4     4     7     7     2     4     7     4     4     7   
30486     0     0     1     0     0     0     1     2     0     1     2     1   
30487     1     1     1     0     1     4     0     0     1     3     1     1   
30488     0     0     0     0     0     0     0     0     0     0     0     0   
30489     0     0     0     0     0     0     0     0     0     0     0     0   

       d_67  d_68  d_69  d_70  d_71  d_72  d_73  d_74  d_75  d_76  d_77  d_78  \
30485     3     4     2     3    10     6     8     5     1     0     2     1   
30486     2     0     1     1     0     1     1     2     0     3     2     1   
30487     1     3     0     1     1     1     2     3     1     1     1     2   
30488     0     0     0     0     0     0     0     0     0     0     0     0   
30489     0     0     0     0     0     0     0     0     0     0     0     0   

       d_79  d_80  d_81  d_82  d_83  d_84  d_85  d_86  d_87  d_88  d_89  d_90  \
30485     0     3     0     2     3     1     1     1     7     1     4     2   


In [ ]:
# Dimensão do df
df_sales.shape

(30490, 1920)

In [ ]:
df_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 30490 entries, 0 to 30489
Columns: 1920 entries, id to d_1913
dtypes: int64(1913), object(7)
memory usage: 446.6+ MB


## Função para observar cada coluna do df_Sales

### ID

In [ ]:
observar(df_sales, 'id')

======== Observações para a coluna 'id' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 30490
  (Mostrando 10 dos 30490 valores únicos)
- Valores Únicos: ['ACCESORIES_1_001_NYC_1' 'ACCESORIES_1_002_NYC_1'
 'ACCESORIES_1_003_NYC_1' 'ACCESORIES_1_004_NYC_1'
 'ACCESORIES_1_005_NYC_1' 'ACCESORIES_1_006_NYC_1'
 'ACCESORIES_1_007_NYC_1' 'ACCESORIES_1_008_NYC_1'
 'ACCESORIES_1_009_NYC_1' 'ACCESORIES_1_010_NYC_1'] ...

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
ACCESORIES_1_001_NYC_1       1
SUPERMARKET_2_202_BOS_3      1
SUPERMARKET_2_214_BOS_3      1
SUPERMARKET_2_213_BOS_3      1
SUPERMARKET_2_212_BOS_3      1
                            ..
HOME_&_GARDEN_1_457_NYC_4    1
HOME_&_GARDEN_1_456_NYC_4    1
HOME_&_GARDEN_1_455_NYC_4    1
HOME_&_GARDEN_1_454_NYC_4    1
SUPERMARKET_3_827_PHI_3      1
Name: id, Length: 30490, dtype: int64


### Item

In [ ]:
observar(df_sales, 'item')

======== Observações para a coluna 'item' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 3049
  (Mostrando 10 dos 3049 valores únicos)
- Valores Únicos: ['ACCESORIES_1_001' 'ACCESORIES_1_002' 'ACCESORIES_1_003'
 'ACCESORIES_1_004' 'ACCESORIES_1_005' 'ACCESORIES_1_006'
 'ACCESORIES_1_007' 'ACCESORIES_1_008' 'ACCESORIES_1_009'
 'ACCESORIES_1_010'] ...

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
ACCESORIES_1_001       10
SUPERMARKET_2_210      10
SUPERMARKET_2_201      10
SUPERMARKET_2_202      10
SUPERMARKET_2_203      10
                       ..
HOME_&_GARDEN_1_464    10
HOME_&_GARDEN_1_465    10
HOME_&_GARDEN_1_466    10
HOME_&_GARDEN_1_467    10
SUPERMARKET_3_827      10
Name: item, Length: 3049, dtype: int64


### category

In [ ]:
observar(df_sales, 'category')

======== Observações para a coluna 'category' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 3
- Valores Únicos: ['ACCESORIES' 'HOME_&_GARDEN' 'SUPERMARKET']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
SUPERMARKET      14370
HOME_&_GARDEN    10470
ACCESORIES        5650
Name: category, dtype: int64


### department

In [ ]:
observar(df_sales, 'department')

======== Observações para a coluna 'department' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 7
- Valores Únicos: ['ACCESORIES_1' 'ACCESORIES_2' 'HOME_&_GARDEN_1' 'HOME_&_GARDEN_2'
 'SUPERMARKET_1' 'SUPERMARKET_2' 'SUPERMARKET_3']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
SUPERMARKET_3      8230
HOME_&_GARDEN_1    5320
HOME_&_GARDEN_2    5150
ACCESORIES_1       4160
SUPERMARKET_2      3980
SUPERMARKET_1      2160
ACCESORIES_2       1490
Name: department, dtype: int64


### store

In [ ]:
observar(df_sales, 'store')

======== Observações para a coluna 'store' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 10
- Valores Únicos: ['Greenwich_Village' 'Harlem' 'Tribeca' 'Brooklyn' 'South_End' 'Roxbury'
 'Back_Bay' 'Midtown_Village' 'Yorktown' 'Queen_Village']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
Greenwich_Village    3049
Harlem               3049
Tribeca              3049
Brooklyn             3049
South_End            3049
Roxbury              3049
Back_Bay             3049
Midtown_Village      3049
Yorktown             3049
Queen_Village        3049
Name: store, dtype: int64


### store_code

In [ ]:
observar(df_sales, 'store_code')

======== Observações para a coluna 'store_code' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 10
- Valores Únicos: ['NYC_1' 'NYC_2' 'NYC_3' 'NYC_4' 'BOS_1' 'BOS_2' 'BOS_3' 'PHI_1' 'PHI_2'
 'PHI_3']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
NYC_1    3049
NYC_2    3049
NYC_3    3049
NYC_4    3049
BOS_1    3049
BOS_2    3049
BOS_3    3049
PHI_1    3049
PHI_2    3049
PHI_3    3049
Name: store_code, dtype: int64


### region

In [ ]:
observar(df_sales, 'region')

======== Observações para a coluna 'region' ========

- Tipo de Dados: object

- Quantidade de Valores Únicos: 3
- Valores Únicos: ['New York' 'Boston' 'Philadelphia']

- Quantidade de Valores Nulos: 0

- Contagem de Valores:
New York        12196
Boston           9147
Philadelphia     9147
Name: region, dtype: int64


## Tratamento das colunas de d_1 a d_1913

## Transformação de df_sales:



*   Como precisamos ter dias como colunas específicas, modifiquei df_sales
*   Eu criei d e sales que contém as vendas daquele dia
*   Isso aumenta drasticamente o tamanho do arquivo csv

Neste caso, o que a função melt está fazendo é converter o dataframe de vendas, que está em formato largo, para um formato longo. Eu mantive as variáveis de identificação como id, item, category, department, store, store_cod  e region. Elas têm, no total, 30.490 valores únicos quando combinadas. Agora, o número total de dias para os quais temos dados é de 1913 dias. Portanto, o dataframe derretido (melted) terá 30.490 x 1913 linhas.






In [ ]:
df_final = pd.melt(df_sales, id_vars=['id','item','category','department','store','store_code', 'region'],\
                   var_name='d', value_name='sold_units')

In [ ]:
# verificando o melt
df_final.head()

id              item    category    department  \
0  ACCESORIES_1_001_NYC_1  ACCESORIES_1_001  ACCESORIES  ACCESORIES_1   
1  ACCESORIES_1_002_NYC_1  ACCESORIES_1_002  ACCESORIES  ACCESORIES_1   
2  ACCESORIES_1_003_NYC_1  ACCESORIES_1_003  ACCESORIES  ACCESORIES_1   
3  ACCESORIES_1_004_NYC_1  ACCESORIES_1_004  ACCESORIES  ACCESORIES_1   
4  ACCESORIES_1_005_NYC_1  ACCESORIES_1_005  ACCESORIES  ACCESORIES_1   

               store store_code    region    d  sold_units        date  \
0  Greenwich_Village      NYC_1  New York  d_1           0  2011-01-29   
1  Greenwich_Village      NYC_1  New York  d_1           0  2011-01-29   
2  Greenwich_Village      NYC_1  New York  d_1           0  2011-01-29   
3  Greenwich_Village      NYC_1  New York  d_1           0  2011-01-29   
4  Greenwich_Village      NYC_1  New York  d_1           0  2011-01-29   

    weekday  weekday_int event  
0  Saturday            1   NaN  
1  Saturday            1   NaN  
2  Saturday            1   NaN  
3  Saturday            1   NaN  
4  Saturday            1   NaN

In [ ]:
# verificando com quantas linhas ficou o df_final
df_final.shape

(58327370, 13)

In [ ]:
df_final = pd.merge(df_final, df_calendar, on='d', how='left')

NameError: ignored

## Transformação de df_prices:

In [ ]:
# Criando uma coluna id na tabela de preços
df_prices["id"] = df_prices["item"].astype(str) + "_" + df_prices["store_code"].astype(str)


In [ ]:
# Criando um dicionário com os preços médios dos itens
mean_prices = df_prices.groupby("id").mean(numeric_only=True)
media_price  = dict(mean_prices["sell_price"])

In [ ]:
# Mapeando os preços e ids para uma nova coluna "price"  e criando mais uma coluna revenue com o faturamento de cada item
df_final["price"] = df_final["id"].map(media_price)
df_final["revenue"] = df_final["price"] * df_final["sold_units"]

In [ ]:
# Renomeando algumas colunas e removendo a coluna d
df_final.rename(columns={"price": "sell_price"}, inplace=True)
df_final.drop('d', axis=1, inplace=True)

In [ ]:
df_final['event'].fillna('sem_evento', inplace=True)


In [ ]:
df_final.head()

id              item    category    department  \
0  ACCESORIES_1_001_NYC_1  ACCESORIES_1_001  ACCESORIES  ACCESORIES_1   
1  ACCESORIES_1_002_NYC_1  ACCESORIES_1_002  ACCESORIES  ACCESORIES_1   
2  ACCESORIES_1_003_NYC_1  ACCESORIES_1_003  ACCESORIES  ACCESORIES_1   
3  ACCESORIES_1_004_NYC_1  ACCESORIES_1_004  ACCESORIES  ACCESORIES_1   
4  ACCESORIES_1_005_NYC_1  ACCESORIES_1_005  ACCESORIES  ACCESORIES_1   

               store store_code    region  sold_units        date   weekday  \
0  Greenwich_Village      NYC_1  New York           0  2011-01-29  Saturday   
1  Greenwich_Village      NYC_1  New York           0  2011-01-29  Saturday   
2  Greenwich_Village      NYC_1  New York           0  2011-01-29  Saturday   
3  Greenwich_Village      NYC_1  New York           0  2011-01-29  Saturday   
4  Greenwich_Village      NYC_1  New York           0  2011-01-29  Saturday   

   weekday_int       event  sell_price  revenue  
0            1  sem_evento   11.018000      0.0  
1            1  sem_evento    5.280000      0.0  
2            1  sem_evento    3.950000      0.0  
3            1  sem_evento    6.022181      0.0  
4            1  sem_evento    3.910232      0.0

In [ ]:
round(df_final.memory_usage().sum() / (1024 * 1024), 1)

(6675.03776550293, 1)

# Exportando df_final

In [ ]:
# Salva o DataFrame como um arquivo CSV no Google Drive
df_final.to_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_final.csv", index=False)

# Importando df_final

In [4]:
df_final = pd.read_csv("/content/drive/MyDrive/ARQUIVOS TFM/df_final.csv")

##  Exploratory Data Analysis

<ul style="list-style-type:circle;">
  <li>O conjunto de dados, generosamente disponibilizado pelo DS MARKET, envolve as vendas unitárias de diversos produtos vendidos nos EUA, organizados na forma de séries temporais agrupadas.</li>
  <li>Mais especificamente, o conjunto de dados envolve as vendas unitárias de 3.049 produtos, classificados em 3 categorias de produtos (ACESSORIES, HOME & GARDEM e SUPERMARKET) e 7 departamentos de produtos, nos quais as categorias acima mencionadas estão desagregadas.</li>
   <li>Os produtos são vendidos em dez lojas, localizadas em três estados ( Boston, Nova york e Philadelphia).</li>
</ul>


In [5]:
# Agrupando e contando a quantidade de itens
group = df_final.groupby(['region','store_code','category','department'],as_index=False)['item'].count()

# Adicionando uma nova coluna para o país
group['country'] = 'United States of America'

# Criando o gráfico treemap
fig = px.treemap(group,
                 path=['country', 'region', 'store_code', 'category', 'department'],
                 values='item',
                 color='item',
                 color_continuous_scale=px.colors.sequential.Sunset,
                 title='DS MARKET: Distribution of items')

# Atualizando o layout e exibindo o gráfico
fig.update_layout(template='plotly')
fig.show()


# Analises de Preços

Aqui estarei estudando sobre os preços dos itens e sua distribuição. Observe que os preços variam semanalmente. Portanto, para estudar a distribuição dos preços, tomei a média deles.

## Distribuição de preços de itens entra lojas

In [6]:
# Agrupando e calculando o preço médio de venda
group_price_store = df_final.groupby(['region', 'store', 'item'], as_index=False)['sell_price'].mean().dropna()

# Criando o gráfico violin
fig = px.violin(group_price_store, x='store', color='region', y='sell_price', box=True, hover_name='item')

# Atualizando os títulos dos eixos e o layout do gráfico
fig.update_xaxes(title_text='Store')
fig.update_yaxes(title_text='Selling Price($)')
fig.update_layout(template='plotly', title='Distribuição de preços de itens das lojas DS MARKET', legend_title_text='Region')

# Exibindo o gráfico
fig.show()


Abaixo estão algumas das observações a partir do gráfico acima:-

<ul style="list-style-type:circle;">
  <li>A distribuição dos preços dos itens é quase uniforme para todas as lojas em Boston, Nova york e Philadelphia.</li>
  <li>O item <b>ACESSORIES_1_225</b> precificado em cerca de 38,54 dólares é o item mais caro sendo vendido nas DS MARKET em BOSTON, nas lojas de ,<b>Roxbury</b> e <b>South_End</b> o item mais caro muda</li>
  <li>O item <b>ACESSORIES_1_060</b> precificado em cerca de 40,58 dólares é o item mais caro sendo vendido nas DS MARKET em  Nova York.</li>
  <li>O item <b>ACESSORIES_1_225</b> precificado em cerca de 40,57 dólares é o item mais caro sendo vendido em <b>Midtown_village</b> ,<b>Queen_Village</b> e <b>Yorktown</b> na Philadelphia</li>
</ul>

## Distribuição de preços de itens entre categorias

In [ ]:
group_price_cat = df_final.groupby(['store', 'category', 'item'], as_index=False)['sell_price'].mean().dropna()
fig = px.violin(group_price_cat, x='store', color='category', y='sell_price', box=True, hover_name='item')
fig.update_xaxes(title_text='Store')
fig.update_yaxes(title_text='Selling Price($)')
fig.update_layout(template='seaborn', title='Distribuição dos preços dos itens nas lojas entre categorias',
                 legend_title_text='Category')
fig.show()


Como pode ser visto no gráfico acima, os itens da categoria supermarket são bastante baratos em comparação com home & Garden e Acessories. home & Garden e Acessories têm quase a mesma faixa de preço basicamente.

# Analises de vendas

## Distribuição de Itens Vendidos por Loja

In [ ]:
# Agrupando os dados por ano, data, loja, código da loja.
# e somando o número total de itens vendidos. Valores nulos são descartados.
group = df_final.groupby(['region', 'date', 'store', 'store_code'], as_index=False)['sold_units'].sum().dropna()

# Ordenando o DataFrame agrupado pela coluna 'region'
group.sort_values(by='region', inplace=True)

# Criando um gráfico de violino com o Plotly, onde o eixo x representa as lojas,
# a cor representa o código da loja, e o eixo y representa o total de itens vendidos.
fig = px.violin(group, x='store', color='store_code', y='sold_units', box=True)
fig.update_xaxes(title_text='Loja')
fig.update_yaxes(title_text='Total de itens vendidos')
fig.update_layout(template='seaborn', title='Distribuição de Itens Vendidos por Loja', legend_title_text='Código da Loja')
fig.show()


Abaixo estão algumas das observações do gráfico acima:

<ul style="list-style-type:circle;">
  <li><b><u>New York</u></b>: <b>Tribeca </b> vendeu o maior número de itens, enquanto <b>Brooklyn </b> vendeu o menor número de itens.</li>
  <li><b><u>Boston </u></b>: <b>Back_Bay </b> e <b> Roxbury </b> venderam o maior número de itens. <b>South_End </b> vendeu o menor número de itens.</li>
  <li><b><u>Philadelphia </u></b>: <b>Yorktown </b> vendeu o maior número de itens, enquanto <b>Queen_Village </b> vendeu o menor número de itens.</li>
  <li><b><u>EUA</u></b>: <b>Tribeca </b> vendeu o maior número de itens, enquanto <b>Brooklyn </b> vendeu o menor número de itens.</li>
</ul>


## Vamos estudar o número de itens vendidos ao longo do tempo em todas as lojas.

In [7]:
# Agregar os dados por data, região e loja
aggregated_df = df_final.groupby(['date', 'region', 'store'], as_index=False)['sold_units'].sum()

# Inicializar o gráfico
fig = go.Figure()

# Iterar pelas regiões únicas
for region in aggregated_df['region'].unique():
    region_data = aggregated_df[aggregated_df['region'] == region]

    # Iterar pelas lojas únicas na região atual
    for store in region_data['store'].unique():
        store_data = region_data[region_data['store'] == store]

        # Adicionar trace para cada loja na região atual
        fig.add_trace(go.Scatter(
            x=store_data['date'],
            y=store_data['sold_units'],
            mode='lines+markers',
            name=f'{store} ({region})'
        ))

# Atualizar o layout
fig.update_layout(
    title='Total de Unidades Vendidas ao Longo do Tempo por Região e Loja',
    xaxis_title='Data',
    yaxis_title='Total de Unidades Vendidas',
    template='seaborn',
    showlegend=True
)

# Exibir o gráfico
pio.show(fig)


In [8]:
# Garantir que a coluna 'date' seja do tipo datetime para a ordenação correta
df_final['date'] = pd.to_datetime(df_final['date'])

# Agrupar por data, loja e somar o número de itens vendidos
vendas_por_data_loja = df_final.groupby(['date', 'store'])['sold_units'].sum().reset_index()

# Criar figura
fig = go.Figure()

# Adicionar uma linha para cada loja
for loja in vendas_por_data_loja['store'].unique():
    dados_loja = vendas_por_data_loja[vendas_por_data_loja['store'] == loja]
    fig.add_trace(go.Scatter(x=dados_loja['date'], y=dados_loja['sold_units'],
                             mode='lines', name=f'Loja {loja}'))

# Atualizar layout do gráfico
fig.update_layout(
    title='Número de Itens Vendidos ao Longo do Tempo por Loja',
    xaxis=dict(title='Data'),
    yaxis=dict(title='Número de Itens Vendidos')
)

# Configurar o template para 'white'
pio.templates.default = "plotly_white"

# Exibir o gráfico
#fig.show()
pio.show(fig)

In [9]:
def plot_metric(df, region, store, metric):
    # Filtragem do DataFrame baseado na região, loja e data.
    store_sales = df[(df['region'] == region) & (df['store'] == store) & (df['date'] <= '2016-04-24')]

    # Categorização de vendas
    accessories_sales = store_sales[store_sales['category'] == 'ACCESORIES']
    home_garden_sales = store_sales[store_sales['category'] == 'HOME_&_GARDEN']
    supermarket_sales = store_sales[store_sales['category'] == 'SUPERMARKET']

    # Agrupando os dados por data e calculando a soma das métricas 'sold_units' e 'revenue'.
    store_sales_grouped = store_sales.groupby(['date'], as_index=False)[['sold_units', 'revenue']].sum()
    accessories_sales_grouped = accessories_sales.groupby(['date'], as_index=False)[['sold_units', 'revenue']].sum()
    home_garden_sales_grouped = home_garden_sales.groupby(['date'], as_index=False)[['sold_units', 'revenue']].sum()
    supermarket_sales_grouped = supermarket_sales.groupby(['date'], as_index=False)[['sold_units', 'revenue']].sum()

    # Criação do Gráfico
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=store_sales_grouped['date'], y=store_sales_grouped[metric], name='Total ' + metric))
    fig.add_trace(go.Scatter(x=accessories_sales_grouped['date'], y=accessories_sales_grouped[metric], name='Accessories ' + metric))
    fig.add_trace(go.Scatter(x=home_garden_sales_grouped['date'], y=home_garden_sales_grouped[metric], name='Home & Garden ' + metric))
    fig.add_trace(go.Scatter(x=supermarket_sales_grouped['date'], y=supermarket_sales_grouped[metric], name='Supermarket ' + metric))

    # Atualização dos eixos e layout do gráfico.
    fig.update_yaxes(title_text='Total items sold' if metric == 'sold_units' else 'Total revenue($)')
    fig.update_layout(template='seaborn', title=store)
    fig.update_layout(
        xaxis=dict(
            range=['2011-01-29', '2016-05-22'],
            rangeselector=dict(
                buttons=list([
                    dict(count=1, label="1m", step="month", stepmode="backward"),
                    dict(count=6, label="6m", step="month", stepmode="backward"),
                    dict(count=1, label="YTD", step="year", stepmode="todate"),
                    dict(count=1, label="1y", step="year", stepmode="backward"),
                    dict(count=2, label="2y", step="year", stepmode="backward"),
                    dict(count=3, label="3y", step="year", stepmode="backward"),
                    dict(count=4, label="4y", step="year", stepmode="backward"),
                    dict(step="all")
                ])
            ),
            rangeslider=dict(
                autorange=True,
            ),
            type="date"
        )
    )
    return fig



In [11]:
cal_data = group.copy()

# Converter a coluna 'date' para datetime
cal_data['date'] = pd.to_datetime(cal_data['date'], dayfirst=True)

cal_data = cal_data[cal_data.date <= '2016-04-24']

# Agora você pode acessar os atributos .dt sem problemas
cal_data['week'] = cal_data.date.dt.isocalendar().week
cal_data['day_name'] = cal_data.date.dt.day_name()


KeyError: ignored

In [ ]:
def calmap(df, store, scale):
    # Filtrar o DataFrame com base na loja
    cal_data = df[df['store'] == store]

    # Converter a coluna 'date' para datetime
    cal_data['date'] = pd.to_datetime(cal_data['date'])

    # Adicionar colunas 'year', 'week', e 'day_name'
    cal_data['year'] = cal_data['date'].dt.year
    cal_data['week'] = cal_data['date'].dt.isocalendar().week
    cal_data['day_name'] = cal_data['date'].dt.day_name()

    # Obter os anos únicos
    years = cal_data['year'].unique().tolist()

    # Criar um subplot para cada ano
    fig = make_subplots(rows=len(years), cols=1, shared_xaxes=True, vertical_spacing=0.005)
    r = 1
    for year in years:
        # Filtrar os dados para o ano atual
        data = cal_data[cal_data['year'] == year]

        # Adicionar um Heatmap ao subplot
        fig.add_trace(go.Heatmap(
            z=data['sold_units'],
            x=data['week'],
            y=data['day_name'],
            hovertext=data['date'].dt.date,
            coloraxis="coloraxis",
            name=str(year),
        ), r, 1)
        fig.update_yaxes(title_text=str(year), tickfont=dict(size=5), row=r, col=1)
        r += 1

    # Atualizar o layout
    fig.update_xaxes(range=[1, 53], tickfont=dict(size=10), nticks=53)
    fig.update_layout(coloraxis={'colorscale': scale})
    fig.update_layout(template='seaborn', title=store)

    return fig

<a id="cal" class="btn btn-primary btn-lg btn-block active" role="button" aria-pressed="true" style="color:white;">New York</a>

<a id='csn'><span class="label label-info">Navegador de Loja</span></a>
<nav aria-label="Navegador de Loja">
  <ul class="pagination">
    <li class="page-item"><a class="page-link" href='#C1'>Brooklyn</a></li>
    <li class="page-item"><a class="page-link" href="#C2">Greenwich_Village</a></li>
    <li class="page-item"><a class="page-link" href="#C3">Harlen</a></li>
    <li class="page-item"><a class="page-link" href="#C4">Tribeca</a></li>
  </ul>
</nav>

### <a id='C1'>Brooklyn</a>

In [ ]:
fig = plot_metric(df_final,'New York','Brooklyn','sold_units')
fig.show()

In [ ]:
fig = plot_metric(df_final,'New York','Brooklyn','revenue')
fig.show()

In [ ]:
fig = calmap(df_final, 'Brooklyn', 'magma')
fig.show()
